In [23]:
import os
import sys
import random
import pickle
import numpy as np
from tqdm import tqdm
import tensorflow as tf 

import jieba.posseg as pseg
from collections import Counter

from bert4keras.backend import K,keras,search_layer
from bert4keras.snippets import ViterbiDecoder,to_array

from data_load import *
from build_model import bert_bilstm_crf


In [31]:
# 固定随机种子
seed = 233
tf.set_random_seed(seed)
np.random.seed(seed)
os.environ['PYTHONHSHSEED'] = str(seed)

# 权重参数
epochs = 6
batch_size = 16
lstm_units = 128
drop_rate = 0.1
learning_rate = 5e-5
max_len =168

#精细训练
fine_train_list = [0 for i in range(8275)]
train_predict_list = []

# 权重路径
config_path = './bert_weight_file/uncased_L-2_H-128_A-2/bert_config.json'
checkpoint_path = './bert_weight_file/uncased_L-2_H-128_A-2/bert_model.ckpt'

# 模型保存路径
model_save_path = './save_model/bert_bilstm_crf.weight'
CRF_save_path = './save_model/CRF.npy'

class NamedEntityRecognizer(ViterbiDecoder):
    """命名实体识别器
    """
    def recognize(self, text):
        tokens = tokenizer.tokenize(text)
        while len(tokens) > max_len:
            tokens.pop(-2)
        mapping = tokenizer.rematch(text, tokens)
        token_ids = tokenizer.tokens_to_ids(tokens)
        segment_ids = [0] * len(token_ids)
        token_ids, segment_ids = to_array([token_ids], [segment_ids]) # ndarray
        nodes = model.predict([token_ids, segment_ids])[0] # [sqe_len,23]
        labels = self.decode(nodes) # id [sqe_len,], [0 0 0 0 0 7 8 8 0 0 0 0 0 0 0]
        entities, starting = [], False
        for i, label in enumerate(labels):
            if label > 0:
                if label % 2 == 1:
                    starting = True
                    entities.append([[i], id2label[(label - 1) // 2]])
                elif starting:
                    entities[-1][0].append(i)
                else:
                    starting = False
            else:
                starting = False
        return [(text[mapping[w[0]][0]:mapping[w[-1]][-1] + 1], l) for w, l in entities], nodes, labels
    
#相等应加set（）中源文本的数量    
def ner_metrics(data,fine_train_list):
    X,Y,Z = 1e-6,1e-6,1e-6
    count = 0
    pos_counts_list = {}
    word_counts_list = {}
    for d in tqdm(data):
        text = ''.join([i[0] for i in d])
        pred,nodes,labels = NER.recognize(text)
        R = set(pred)
        T = set([tuple(i) for i in d if i[1] != 'O'])
        
        # 统计词性分布
        if len(T) > 0 :
            words = pseg.cut(text)
            pos_counts = {}
            word_counts = {}
            for t_word, t_pos in T:
                pos_counts[t_word] = {pos: 0 for pos in set([p for w, p in words if w == t_word])}
                word_counts[t_word] = 0
                for word, pos in words:
                    if word == t_word:
                        pos_counts[t_word][pos] += 1
                        word_counts[t_word] += 1
            pos_counts_list.update(pos_counts)
            word_counts_list.update(word_counts)
        
        
        # 便于T和R做交集
        m = []
        for i in T:
            for j in i[0]:
                m.append((j,i[1]))
        T = set(m)
        
        # 填充train_predict_list,更新fine_train_list
        if len(T) > 0 :  
            if len(train_predict_list) < 8275:
                train_predict_list.append(R&T)
            else:
                if len(R&T) > fine_train_list[count]:
#                     print('text: ',text)
#                     print('T: ',T)
#                     print('R&T: ',R&T)
                    train_predict_list[count] = R&T
            if len(R&T) > fine_train_list[count]:
                fine_train_list[count] = len(R&T)
            
            if len(T)>len(R):
                print(text)
                print('R: ',R)
                print('T: ',T)
                print('nodes: ',nodes)
            
            
        if len(T) < fine_train_list[count]:
            print(False)
            print('text: ',text)
            print('T: ',T)
            print('R&T: ',R&T)
            print('fine_train_list[count]: ',fine_train_list[count])
            print()

        X += fine_train_list[count]
        if len(R) < fine_train_list[count]:
            Y += fine_train_list[count]
        else:
            Y += len(R)
            
        Z += len(T)
        count += 1
    
    pos_ratios = {}
    for t_word, pos_count in pos_counts_list.items():
        total_count = word_counts_list[t_word]
        pos_ratios[t_word] = {pos: count / total_count for pos, count in pos_count.items()}
    
    f1,precision,recall = 2 * X / (Y + Z),X / Y,X / Z
    return f1,precision,recall,pos_ratios

class Evaluator(keras.callbacks.Callback):
    def __init__(self):
        super(Evaluator, self).__init__()
        self.best_val_f1 = 0
    def on_epoch_end(self, epoch,logs=None):
        NER.trans = K.eval(CRF.trans) # 可能有错
        f1, precision, recall = ner_metrics(valid_data,fine_train_list)
        if f1 > self.best_val_f1:
            model.save_weights(model_save_path)
            self.best_val_f1 = f1
            print('save model to {}'.format(checkpoint_path))
        else:
            global learning_rate
            learning_rate = learning_rate / 5
        print(
              'valid: f1: %.5f, precision: %.5f, recall: %.5f, best f1: %.5f\n' %
              (f1,precision,recall,self.best_val_f1)
        )
model,CRF = bert_bilstm_crf(config_path,checkpoint_path,num_labels,lstm_units,drop_rate,learning_rate)
model.load_weights(model_save_path)
NER = NamedEntityRecognizer(trans=K.eval(CRF.trans), starts=[0], ends=[0])
seg = pkuseg.pkuseg(model_name='medicine',postag=True)

train_data,_ = load_data('./ner_data/train/train.txt',128)
valid_data,_ = load_data('./ner_data/dev/test.txt',128)

train_generator = data_generator(train_data, batch_size)
valid_generator = data_generator(valid_data, batch_size*5)

f1,precision,recall,pos_ratios = ner_metrics(valid_data,fine_train_list)

  1%|▍                                                                               | 50/8275 [00:00<01:33, 88.05it/s]

医生：嗯啊，宝贝主要是呕吐对吗
R:  set()
T:  {('吐', 'Symptom'), ('呕', 'Symptom')}
nodes:  [[ 9.305901          -inf        -inf        -inf        -inf        -inf
         -inf        -inf        -inf        -inf        -inf]
 [ 9.25873     0.9204125   0.          1.287583    0.          0.
   0.          0.01588435  0.          1.9421664   0.        ]
 [ 9.619988    1.0708485   0.          0.81527966  0.          0.
   0.          0.          0.          1.2803397   0.        ]
 [ 9.341177    0.          0.          0.          0.          0.
   0.          0.          0.          0.9902713   0.        ]
 [ 3.973535    3.3591607   0.          2.7682254   0.          2.4510977
   0.          1.6176498   0.          5.9452977   0.        ]
 [ 4.3777175   3.217806    0.          3.022347    0.          2.3194458
   0.          2.201526    0.          5.688552    0.        ]
 [ 9.399867    0.          0.          0.          0.          0.
   0.          0.          0.          0.35279623  0.        ]


  1%|▉                                                                              | 92/8275 [00:01<00:59, 136.92it/s]

医生：观察呕吐次数，大便次数，如果两天症状不缓解或者加重，及时带宝贝去儿内科就诊
R:  set()
T:  {('吐', 'Symptom'), ('呕', 'Symptom')}
nodes:  [[10.083617          -inf        -inf        -inf        -inf        -inf
         -inf        -inf        -inf        -inf        -inf]
 [10.554995    0.          0.          0.30347294  0.          0.
   0.          0.          0.          0.09183832  0.        ]
 [10.976237    0.66474664  0.          0.12251196  0.          0.
   0.          0.          0.          0.2516042   0.        ]
 [10.589169    0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.        ]
 [ 4.302683    3.9700015   0.          3.4759958   0.          3.9093668
   0.          2.0857844   0.          4.2068686   0.        ]
 [ 5.4590936   3.9878628   0.          3.6664076   0.          3.8904674
   0.          2.3959324   0.          3.6832423   0.        ]
 [ 5.1860414   4.281431    0.          4.128024    0.          4.3156023
   0.          2.2391696   0.  

  2%|█▎                                                                            | 140/8275 [00:01<00:44, 183.94it/s]

...

100%|████████████████████████████████████████████████████████████████████████████▋| 8241/8275 [00:45<00:00, 163.65it/s]


R:  set()
T:  {('吸', 'Symptom'), ('染', 'Symptom'), ('呼', 'Symptom'), ('道', 'Symptom'), ('感', 'Symptom')}
nodes:  [[9.84444714e+00           -inf           -inf           -inf
            -inf           -inf           -inf           -inf
            -inf           -inf           -inf]
 [1.14978180e+01 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 3.15313727e-01
  0.00000000e+00 1.00278759e+00 0.00000000e+00]
 [1.13764257e+01 4.41460788e-01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 4.74937186e-02
  0.00000000e+00 4.87090558e-01 0.00000000e+00]
 [1.10154285e+01 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 6.17032349e-01
  0.00000000e+00 1.73980042e-01 0.00000000e+00]
 [5.98059559e+00 4.24718618e+00 0.00000000e+00 3.09013700e+00
  0.00000000e+00 3.18639398e+00 0.00000000e+00 2.69203973e+00
  0.00000000e+00 5.10311508e+00 0.00000000e+00]
 [7.56875753e+00 3.9652400

100%|█████████████████████████████████████████████████████████████████████████████| 8275/8275 [00:45<00:00, 180.28it/s]

医生：母亲一定要避免太油腻的食物给宝宝口服妈咪爱。
R:  set()
T:  {('妈', 'Drug'), ('咪', 'Drug'), ('爱', 'Drug')}
nodes:  [[10.511335          -inf        -inf        -inf        -inf        -inf
         -inf        -inf        -inf        -inf        -inf]
 [11.015321    0.98524797  0.          0.7766115   0.          0.
   0.          0.1669022   0.          1.143606    0.        ]
 [10.780162    1.2927576   0.          0.9069837   0.          0.
   0.          0.          0.          0.8268703   0.        ]
 [10.328628    0.11612355  0.          0.          0.          0.
   0.          0.          0.          0.5792405   0.        ]
 [ 3.4478636   3.3039753   0.          2.6322346   0.          2.775328
   0.          2.7832139   0.          5.546022    0.        ]
 [ 3.590383    3.5117495   0.          2.97368     0.          3.0036747
   0.          2.6884341   0.          5.022587    0.        ]
 [ 8.739757    3.16243     0.          0.8981038   0.          0.
   0.          0.          0.          1.0930

ZeroDivisionError: division by zero

In [32]:
pos_ratios

{'v': 0.38319141058867084,
 'n': 0.4013328396890041,
 'a': 0.02073306182895224,
 'nr': 0.06664198445020363,
 'd': 0.008145131432802665,
 'l': 0.03258052573121066,
 'vn': 0.050351721584598295,
 'm': 0.006664198445020363,
 'nz': 0.017030729359496483,
 'o': 0.0007404664938911515,
 'ns': 0.0022213994816734544,
 'i': 0.0033320992225101815,
 'nrt': 0.00259163272861903,
 'b': 0.001480932987782303,
 'j': 0.001480932987782303,
 'eng': 0.001480932987782303}

In [13]:
text = seg.cut('医生：宝宝最多见的就是消化不良，腹部受冷，或者是拉肚子还有就是感冒引起的。所以一定要给宝宝腹部保暖，口服妈咪爱，思密达，宝宝一贴灵，平常一定要多注意，给宝宝按摩腹部，母亲一定要避免生冷食物，也就是告诉你一定要从多方面来注意。')
print(text)

[('医生', 'n'), ('：', 'w'), ('宝宝', 'n'), ('最多', 'd'), ('见', 'v'), ('的', 'u'), ('就是', 'd'), ('消化', 'v'), ('不良', 'a'), ('，', 'w'), ('腹部', 'n'), ('受', 'v'), ('冷', 'a'), ('，', 'w'), ('或者', 'c'), ('是', 'v'), ('拉肚子', 'n'), ('还有', 'v'), ('就是', 'd'), ('感冒', 'v'), ('引起', 'v'), ('的', 'u'), ('。', 'w'), ('所以', 'c'), ('一定', 'd'), ('要', 'v'), ('给', 'p'), ('宝宝', 'nz'), ('腹部', 'n'), ('保暖', 'a'), ('，', 'w'), ('口服', 'n'), ('妈咪爱', 'v'), ('，', 'w'), ('思密达', 'v'), ('，', 'w'), ('宝宝一贴灵', 'n'), ('，', 'w'), ('平常', 'n'), ('一定', 'd'), ('要', 'v'), ('多', 'ad'), ('注意', 'v'), ('，', 'w'), ('给', 'p'), ('宝宝', 'n'), ('按', 'p'), ('摩腹部', 'n'), ('，', 'w'), ('母亲', 'n'), ('一定', 'd'), ('要', 'v'), ('避免', 'v'), ('生冷', 'a'), ('食物', 'n'), ('，', 'w'), ('也', 'd'), ('就是', 'd'), ('告诉', 'v'), ('你', 'r'), ('一定', 'd'), ('要', 'v'), ('从', 'p'), ('多方面', 'd'), ('来', 'v'), ('注意', 'v'), ('。', 'w')]


In [7]:
text = seg.cut('医生：嗯像支气管炎气管炎和肺炎，他们都是ｈｔ的位置不一样其实大方向治疗的方向是一样的，只是病程的长短不一样')
print(text)

[('医生', 'n'), ('：', 'w'), ('嗯', 'v'), ('像', 'v'), ('支气管', 'n'), ('炎气管炎', 'n'), ('和', 'c'), ('肺炎', 'n'), ('，', 'w'), ('他们', 'r'), ('都', 'd'), ('是', 'v'), ('ｈｔ', 'i'), ('的', 'u'), ('位置', 'n'), ('不', 'd'), ('一样', 'a'), ('其', 'r'), ('实大', 'a'), ('方向', 'n'), ('治疗', 'v'), ('的', 'u'), ('方向', 'n'), ('是', 'v'), ('一样', 'a'), ('的', 'u'), ('，', 'w'), ('只是', 'c'), ('病程', 'n'), ('的', 'u'), ('长短', 'n'), ('不', 'd'), ('一样', 'a')]


In [12]:
R={('炎', 'Symptom'), ('肺', 'Symptom')}
T={('气', 'Symptom'), ('管', 'Symptom'), ('炎', 'Symptom'), ('支', 'Symptom'), ('肺', 'Symptom')}
print((R|T)-(R&T))

{('气', 'Symptom'), ('管', 'Symptom'), ('支', 'Symptom')}


In [30]:
import jieba
import jieba.posseg as pseg

jieba.enable_paddle() 
seg_list = pseg.cut('医生：宝宝最多见的就是消化不良，腹部受冷，或者是拉肚子还有就是感冒引起的。所以一定要给宝宝腹部保暖，口服妈咪爱，思密达，宝宝一贴灵，平常一定要多注意，给宝宝按摩腹部，母亲一定要避免生冷食物，也就是告诉你一定要从多方面来注意',use_paddle=True)
for word, flag in seg_list:
    print('%s %s' % (word, flag))
 


Paddle enabled successfully......


医生 n
： v
宝宝 n
最多 d
见 v
的 u
就是 v
消化不良， nz
腹部 n
受 v
冷， PER
或者 c
是 v
拉肚子 v
还有 v
就是 v
感冒 n
引起 v
的 u
。 n
所以 c
一定要 v
给 p
宝宝 n
腹部 n
保暖 vn
， n
口服 v
妈咪爱，思密达， nz
宝宝 n
一 d
贴 v
灵， n
平常 d
一定要 v
多 ad
注意 v
， v
给 p
宝宝 n
按摩 v
腹部 n
， v
母亲 n
一定要 v
避免 v
生冷 a
食物 n
， n
也 d
就是 v
告诉你 v
一定要 v
从 p
多方面 n
来 v
注意 v
